In [1]:
import pandas as pd
import numpy as np
import os

DATA_DIR = os.path.join("..", "data")

In [2]:
detailed_tourney_games_df = pd.concat(
    [
        pd.read_csv(os.path.join(DATA_DIR, "MNCAATourneyDetailedResults.csv")).assign(
            League="M"
        ),
        pd.read_csv(os.path.join(DATA_DIR, "WNCAATourneyDetailedResults.csv")).assign(
            League="W"
        ),
    ]
)

detailed_tourney_games_df.sample(5, random_state=1)

Season  DayNum  WTeamID  WScore  LTeamID  LScore WLoc  NumOT  WFGM  \
808     2015     137     1320      71     1461      54    N      0    23   
682     2021     146     3257      60     3332      42    N      0    26   
1114    2019     154     1438      85     1403      77    N      1    27   
718     2022     138     3261      83     3238      77    H      0    30   
1217    2022     138     1116      53     1308      48    N      0    14   

      WFGA  ...  LFTM  LFTA  LOR  LDR  LAst  LTO  LStl  LBlk  LPF  League  
808     50  ...     3     9    4   18    14   12     2     3   17       M  
682     63  ...     4     5   14   23     7   14     5     6   10       W  
1114    59  ...    13    15    9   23     9    8     6     3   18       M  
718     74  ...    19    29   12   28    11   15     5     4   23       W  
1217    51  ...     6    10    4   32     8   17     4     4   15       M  

[5 rows x 35 columns]

In [3]:
detailed_reg_games_df = pd.concat(
    [
        pd.read_csv(os.path.join(DATA_DIR, "MRegularSeasonDetailedResults.csv")).assign(
            League="M"
        ),
        pd.read_csv(os.path.join(DATA_DIR, "WRegularSeasonDetailedResults.csv")).assign(
            League="W"
        ),
    ]
)

detailed_reg_games_df.sample(5, random_state=1)

Season  DayNum  WTeamID  WScore  LTeamID  LScore WLoc  NumOT  WFGM  \
27948     2008     110     1193      60     1180      51    A      0    22   
88315     2020      19     1345      81     1240      49    H      0    31   
1536      2003      59     1272      72     1116      67    A      0    23   
104465    2023      66     1186      92     1340      80    H      0    30   
85458     2019      86     1292      71     1412      65    H      0    25   

        WFGA  ...  LFTM  LFTA  LOR  LDR  LAst  LTO  LStl  LBlk  LPF  League  
27948     52  ...     7    12   14   20    13   10     4     3   16       M  
88315     56  ...    12    21   13   21    10    8     4     0   19       M  
1536      50  ...    14    20    5   17     8   13    10     2   25       M  
104465    51  ...    10    13   12   17    15   11    11     2   20       M  
85458     57  ...    15    22    5   27     7   11    11     2   14       M  

[5 rows x 35 columns]

## Concat

In [4]:
# here we are making it such that each game has two rows, where each one is a team view of the game with
# opposing metrics.

detailed_metrics = {
    "Score",
    # "Loc",
    "FGM",
    "FGA",
    "FGM3",
    "FTM",
    "FTA",
    "OR",
    "DR",
    "Ast",
    "Blk",
    "TO",
    "Stl",
    "PF",
}

w_renamed_cols = {f"W{col}": f"Team{col}" for col in detailed_metrics} | {
    f"L{col}": f"Opp{col}" for col in detailed_metrics
}
l_renamed_cols = {f"L{col}": f"Team{col}" for col in detailed_metrics} | {
    f"W{col}": f"Opp{col}" for col in detailed_metrics
}

In [5]:
detailed_reg_games_df = pd.concat(
    [
        (
            # detailed_reg_games_df[[col for col in detailed_reg_games_df.columns if col != "LTeamID"]]
            detailed_reg_games_df[[col for col in detailed_reg_games_df.columns]]
            .assign(GameResult="W")
            .rename(
                columns=w_renamed_cols | {"WTeamID": "TeamID", "LTeamID": "OppTeamID"}
            )
        ),
        (
            # detailed_reg_games_df[[col for col in detailed_reg_games_df.columns if col != "WTeamID"]]
            detailed_reg_games_df[[col for col in detailed_reg_games_df.columns]]
            .assign(GameResult="L")
            .rename(
                columns=l_renamed_cols | {"LTeamID": "TeamID", "WTeamID": "OppTeamID"}
            )
        ),
    ]
).reset_index(drop=True)

detailed_reg_games_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 373324 entries, 0 to 373323
Data columns (total 36 columns):
 #   Column      Non-Null Count   Dtype 
---  ------      --------------   ----- 
 0   Season      373324 non-null  int64 
 1   DayNum      373324 non-null  int64 
 2   TeamID      373324 non-null  int64 
 3   TeamScore   373324 non-null  int64 
 4   OppTeamID   373324 non-null  int64 
 5   OppScore    373324 non-null  int64 
 6   WLoc        373324 non-null  object
 7   NumOT       373324 non-null  int64 
 8   TeamFGM     373324 non-null  int64 
 9   TeamFGA     373324 non-null  int64 
 10  TeamFGM3    373324 non-null  int64 
 11  WFGA3       373324 non-null  int64 
 12  TeamFTM     373324 non-null  int64 
 13  TeamFTA     373324 non-null  int64 
 14  TeamOR      373324 non-null  int64 
 15  TeamDR      373324 non-null  int64 
 16  TeamAst     373324 non-null  int64 
 17  TeamTO      373324 non-null  int64 
 18  TeamStl     373324 non-null  int64 
 19  TeamBlk     373324 non-

In [6]:
# do the same thing for the tournament games
detailed_tourney_games_df = pd.concat(
    [
        (
            # detailed_tourney_games_df[[col for col in detailed_tourney_games_df.columns if col != "LTeamID"]]
            detailed_tourney_games_df[
                [col for col in detailed_tourney_games_df.columns]
            ]
            .assign(GameResult="W")
            .rename(
                columns=w_renamed_cols | {"WTeamID": "TeamID", "LTeamID": "OppTeamID"}
            )
        ),
        (
            # detailed_tourney_games_df[[col for col in detailed_tourney_games_df.columns if col != "WTeamID"]]
            detailed_tourney_games_df[
                [col for col in detailed_tourney_games_df.columns]
            ]
            .assign(GameResult="L")
            .rename(
                columns=l_renamed_cols | {"LTeamID": "TeamID", "WTeamID": "OppTeamID"}
            )
        ),
    ]
).reset_index(drop=True)

detailed_tourney_games_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4284 entries, 0 to 4283
Data columns (total 36 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   Season      4284 non-null   int64 
 1   DayNum      4284 non-null   int64 
 2   TeamID      4284 non-null   int64 
 3   TeamScore   4284 non-null   int64 
 4   OppTeamID   4284 non-null   int64 
 5   OppScore    4284 non-null   int64 
 6   WLoc        4284 non-null   object
 7   NumOT       4284 non-null   int64 
 8   TeamFGM     4284 non-null   int64 
 9   TeamFGA     4284 non-null   int64 
 10  TeamFGM3    4284 non-null   int64 
 11  WFGA3       4284 non-null   int64 
 12  TeamFTM     4284 non-null   int64 
 13  TeamFTA     4284 non-null   int64 
 14  TeamOR      4284 non-null   int64 
 15  TeamDR      4284 non-null   int64 
 16  TeamAst     4284 non-null   int64 
 17  TeamTO      4284 non-null   int64 
 18  TeamStl     4284 non-null   int64 
 19  TeamBlk     4284 non-null   int64 
 20  TeamPF  

In [7]:
for col in detailed_metrics:
    detailed_reg_games_df[f"{col}Diff"] = detailed_reg_games_df.apply(
        lambda row: row[f"Team{col}"] - row[f"Opp{col}"],
        axis=1,
    )

    detailed_tourney_games_df[f"{col}Diff"] = detailed_tourney_games_df.apply(
        lambda row: row[f"Team{col}"] - row[f"Opp{col}"],
        axis=1,
    )

In [8]:
detailed_reg_games_df.sample(5, random_state=1)

Season  DayNum  TeamID  TeamScore  OppTeamID  OppScore WLoc  NumOT  \
337067    2017      74    3158         56       3189        84    A      0   
100732    2022     103    1439         71       1393        59    H      0   
83150     2019      26    1180         82       1352        69    H      0   
345009    2019       4    3435         58       3292        65    H      0   
318707    2013     128    3322         45       3270        63    N      0   

        TeamFGM  TeamFGA  ...  FTADiff  PFDiff  ScoreDiff  FGADiff  BlkDiff  \
337067       21       55  ...      -11       9        -28      -12        1   
100732       23       60  ...       17      -9         12       -4        2   
83150        27       58  ...       10      -5         13       -6        2   
345009       19       55  ...      -11       7         -7       13       -3   
318707       20       51  ...      -11       2        -18        3        1   

        FGM3Diff  ORDiff  StlDiff  AstDiff  DRDiff  
337067        -3     -11       -7       -1      -4  
100732        -2      -1        4       11       1  
83150          1       4       -5        1      13  
345009        -1       2       -3        4      -7  
318707        -3       2       -7        2      -3  

[5 rows x 49 columns]

In [9]:
detailed_reg_games_df["Win"] = detailed_reg_games_df.apply(
    lambda row: 0 if row["GameResult"] == "L" else 1,
    axis=1,
)

detailed_reg_games_df["OppWin"] = detailed_reg_games_df.apply(
    lambda row: 1 if row["GameResult"] == "L" else 0,
    axis=1,
)

detailed_tourney_games_df["Win"] = detailed_tourney_games_df.apply(
    lambda row: 0 if row["GameResult"] == "L" else 1,
    axis=1,
)

detailed_tourney_games_df["OppWin"] = detailed_tourney_games_df.apply(
    lambda row: 1 if row["GameResult"] == "L" else 0,
    axis=1,
)

In [10]:
# combine the two detailed game dataframes into one for future use

all_detailed_games_df = pd.concat(
    [
        detailed_reg_games_df.assign(GameType="reg"),
        detailed_tourney_games_df.assign(GameType="tourney"),
    ]
)

In [11]:
all_detailed_games_df["OppTeamID"]

0       1328
1       1393
2       1437
3       1457
4       1208
        ... 
4279    3376
4280    3439
4281    3234
4282    3261
4283    3261
Name: OppTeamID, Length: 377608, dtype: int64

## Aggregation

In [12]:
exclude_agg_cols = {
    "TeamID",
    "Season",
    "League",
    "GameResult",
    "OppLoc",
    "TeamLoc",
    "Season",
    "DayNum",
    # "OppTeamID",
}

agg_funcs = [
    np.min,
    np.max,
    np.std,
    np.median,
    np.mean,
]

In [13]:
team_reg_agg = (
    detailed_reg_games_df.groupby(["TeamID", "Season", "League"])
    .agg(
        {
            col: agg_funcs
            for col in detailed_reg_games_df.select_dtypes("number").columns
            if col not in exclude_agg_cols
        }
    )
    .reset_index()
)

team_reg_agg.columns = [" ".join(col).strip() for col in team_reg_agg.columns.values]

team_reg_agg.sample(10, random_state=1)

TeamID  Season League  TeamScore min  TeamScore max  TeamScore std  \
12348    3430    2012      W             41             78      10.808339   
6900     1431    2018      M             33             88      12.283247   
4406     1315    2014      M             43             95      10.019980   
4233     1307    2005      M             53            101      12.911860   
3407     1266    2008      M             51            100      11.841315   
5190     1352    2016      M             44             89      10.298567   
1892     1194    2005      M             45            104      14.194618   
10020    3270    2021      W             24             80      13.385137   
9567     3240    2014      W             43             84      11.319009   
12617    3452    2011      W             39             90      12.518374   

       TeamScore median  TeamScore mean  OppTeamID min  OppTeamID max  ...  \
12348              61.0       58.965517           3129           3451  ...   
6900               67.0       66.466667           1111           1450  ...   
4406               72.0       73.000000           1132           1458  ...   
4233               77.0       75.870968           1102           1461  ...   
3407               75.5       75.906250           1153           1458  ...   
5190               67.0       65.062500           1102           1464  ...   
1892               76.0       76.777778           1125           1424  ...   
10020              53.0       55.476190           3124           3418  ...   
9567               62.5       63.593750           3120           3404  ...   
12617              65.0       65.750000           3148           3438  ...   

       Win min  Win max   Win std  Win median  Win mean  OppWin min  \
12348        0        1  0.508548         0.0  0.482759           0   
6900         0        1  0.479463         0.0  0.333333           0   
4406         0        1  0.508001         0.0  0.483871           0   
4233         0        1  0.401610         1.0  0.806452           0   
3407         0        1  0.456803         1.0  0.718750           0   
5190         0        1  0.470929         0.0  0.312500           0   
1892         0        1  0.492103         0.0  0.370370           0   
10020        0        1  0.462910         0.0  0.285714           0   
9567         0        1  0.504016         0.0  0.437500           0   
12617        0        1  0.456803         1.0  0.718750           0   

       OppWin max  OppWin std  OppWin median  OppWin mean  
12348           1    0.508548            1.0     0.517241  
6900            1    0.479463            1.0     0.666667  
4406            1    0.508001            1.0     0.516129  
4233            1    0.401610            0.0     0.193548  
3407            1    0.456803            0.0     0.281250  
5190            1    0.470929            1.0     0.687500  
1892            1    0.492103            1.0     0.629630  
10020           1    0.462910            1.0     0.714286  
9567            1    0.504016            1.0     0.562500  
12617           1    0.456803            0.0     0.281250  

[10 rows x 228 columns]

In [14]:
# aggregate the same metrics for the tournament dataset

team_tourney_agg = (
    detailed_tourney_games_df.groupby(["TeamID", "Season", "League"])
    .agg(
        {
            col: agg_funcs
            for col in detailed_tourney_games_df.select_dtypes("number").columns
            if col not in exclude_agg_cols
        }
    )
    .reset_index()
)

team_tourney_agg.columns = [
    " ".join(col).strip() for col in team_tourney_agg.columns.values
]

team_tourney_agg.sample(10, random_state=1)

TeamID  Season League  TeamScore min  TeamScore max  TeamScore std  \
995     1390    2008      M             62             82      10.408330   
1601    3226    2021      W             63             63            NaN   
1805    3301    2023      W             63             63            NaN   
952     1373    2009      M             72             74       1.414214   
924     1361    2012      M             65             65            NaN   
1381    3124    2014      W             69             90       9.912114   
1266    1452    2021      M             72             84       8.485281   
1810    3304    2015      W             69             69            NaN   
697     1301    2023      M             63             63            NaN   
763     1323    2003      M             68             71       1.527525   

      TeamScore median  TeamScore mean  OppTeamID min  OppTeamID max  ...  \
995               77.0       73.666667           1165           1400  ...   
1601              63.0       63.000000           3246           3246  ...   
1805              63.0       63.000000           3343           3343  ...   
952               73.0       73.000000           1257           1326  ...   
924               65.0       65.000000           1301           1301  ...   
1381              81.0       80.250000           3143           3443  ...   
1266              78.0       78.000000           1287           1393  ...   
1810              69.0       69.000000           3393           3393  ...   
697               63.0       63.000000           1166           1166  ...   
763               70.0       69.666667           1112           1454  ...   

      Win min  Win max   Win std  Win median  Win mean  OppWin min  \
995         0        1  0.577350         1.0  0.666667           0   
1601        0        0       NaN         0.0  0.000000           1   
1805        0        0       NaN         0.0  0.000000           1   
952         0        1  0.707107         0.5  0.500000           0   
924         0        0       NaN         0.0  0.000000           1   
1381        0        1  0.500000         1.0  0.750000           0   
1266        0        1  0.707107         0.5  0.500000           0   
1810        0        0       NaN         0.0  0.000000           1   
697         0        0       NaN         0.0  0.000000           1   
763         0        1  0.577350         1.0  0.666667           0   

      OppWin max  OppWin std  OppWin median  OppWin mean  
995            1    0.577350            0.0     0.333333  
1601           1         NaN            1.0     1.000000  
1805           1         NaN            1.0     1.000000  
952            1    0.707107            0.5     0.500000  
924            1         NaN            1.0     1.000000  
1381           1    0.500000            0.0     0.250000  
1266           1    0.707107            0.5     0.500000  
1810           1         NaN            1.0     1.000000  
697            1         NaN            1.0     1.000000  
763            1    0.577350            0.0     0.333333  

[10 rows x 228 columns]

## Join Aggregated w/ Attributes

In [15]:
conference_df = pd.concat(
    [
        pd.read_csv(os.path.join(DATA_DIR, "MNCAATourneySeeds.csv")).assign(League="M"),
        pd.read_csv(os.path.join(DATA_DIR, "WNCAATourneySeeds.csv")).assign(League="W"),
    ]
)

team_conf_seeds_df = conference_df.merge(
    right=(
        pd.concat(
            [
                pd.read_csv(os.path.join(DATA_DIR, "MTeamConferences.csv")).assign(
                    League="M"
                ),
                pd.read_csv(os.path.join(DATA_DIR, "WTeamConferences.csv")).assign(
                    League="W"
                ),
            ]
        )
    ),
    on=["League", "Season", "TeamID"],
    how="left",
).merge(right=(
    pd.concat([
        pd.read_csv(os.path.join(DATA_DIR, "MTeams.csv")),
        pd.read_csv(os.path.join(DATA_DIR, "WTeams.csv")),
    ])),
    on="TeamID",
)

team_conf_seeds_df["ChalkSeed"] = team_conf_seeds_df.apply(
    lambda row: int(row["Seed"][1:].replace("a", "").replace("b", "")),
    axis=1,
)

team_conf_seeds_df.sample(5, random_state=1)

Season Seed  TeamID League  ConfAbbrev        TeamName  FirstD1Season  \
3591    2004  X02    3243      W  big_twelve       Kansas St            NaN   
3528    2013  Y01    3124      W  big_twelve          Baylor            NaN   
1891    2003  W02    1448      M         acc     Wake Forest         1985.0   
778     2019  Y01    1314      M         acc  North Carolina         1985.0   
2932    2019  X05    3266      W    big_east       Marquette            NaN   

      LastD1Season  ChalkSeed  
3591           NaN          2  
3528           NaN          1  
1891        2024.0          2  
778         2024.0          1  
2932           NaN          5

In [16]:
# merge the tournament aggregated metrics with the regular season aggregated metrics
team_agg_df = pd.merge(
    left=team_reg_agg,
    right=team_tourney_agg,
    how="left",
    on=["TeamID", "Season", "League"],
    suffixes=(" reg", " tourney"),
    validate="1:1",
)

team_agg_df.sample(10, random_state=1)

TeamID  Season League  TeamScore min reg  TeamScore max reg  \
12348    3430    2012      W                 41                 78   
6900     1431    2018      M                 33                 88   
4406     1315    2014      M                 43                 95   
4233     1307    2005      M                 53                101   
3407     1266    2008      M                 51                100   
5190     1352    2016      M                 44                 89   
1892     1194    2005      M                 45                104   
10020    3270    2021      W                 24                 80   
9567     3240    2014      W                 43                 84   
12617    3452    2011      W                 39                 90   

       TeamScore std reg  TeamScore median reg  TeamScore mean reg  \
12348          10.808339                  61.0           58.965517   
6900           12.283247                  67.0           66.466667   
4406           10.019980                  72.0           73.000000   
4233           12.911860                  77.0           75.870968   
3407           11.841315                  75.5           75.906250   
5190           10.298567                  67.0           65.062500   
1892           14.194618                  76.0           76.777778   
10020          13.385137                  53.0           55.476190   
9567           11.319009                  62.5           63.593750   
12617          12.518374                  65.0           65.750000   

       OppTeamID min reg  OppTeamID max reg  ...  Win min tourney  \
12348               3129               3451  ...              NaN   
6900                1111               1450  ...              NaN   
4406                1132               1458  ...              NaN   
4233                1102               1461  ...              0.0   
3407                1153               1458  ...              0.0   
5190                1102               1464  ...              NaN   
1892                1125               1424  ...              NaN   
10020               3124               3418  ...              NaN   
9567                3120               3404  ...              NaN   
12617               3148               3438  ...              0.0   

       Win max tourney  Win std tourney  Win median tourney  Win mean tourney  \
12348              NaN              NaN                 NaN               NaN   
6900               NaN              NaN                 NaN               NaN   
4406               NaN              NaN                 NaN               NaN   
4233               0.0              NaN                 0.0               0.0   
3407               1.0         0.707107                 0.5               0.5   
5190               NaN              NaN                 NaN               NaN   
1892               NaN              NaN                 NaN               NaN   
10020              NaN              NaN                 NaN               NaN   
9567               NaN              NaN                 NaN               NaN   
12617              1.0         0.707107                 0.5               0.5   

       OppWin min tourney  OppWin max tourney  OppWin std tourney  \
12348                 NaN                 NaN                 NaN   
6900                  NaN                 NaN                 NaN   
4406                  NaN                 NaN                 NaN   
4233                  1.0                 1.0                 NaN   
3407                  0.0                 1.0            0.707107   
5190                  NaN                 NaN                 NaN   
1892                  NaN                 NaN                 NaN   
10020                 NaN                 NaN                 NaN   
9567                  NaN                 NaN                 NaN   
12617                 0.0                 1.0            0.707107   

       OppWin median tourney  OppWin mean tourney  
1

In [17]:
# merge the team_conf_seeds_df with team attributes into the aggregated data
team_agg_df2 = pd.merge(
    left=team_agg_df,
    right=team_conf_seeds_df[team_conf_seeds_df["Season"] >= 2003],
    on=["TeamID", "Season", "League"],
    how="outer",
    validate="1:1",
)

team_agg_df2 = team_agg_df2[team_agg_df2["Season"] >= 2003]

In [18]:
team_agg_df2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 13305 entries, 0 to 13304
Columns: 459 entries, TeamID to ChalkSeed
dtypes: float64(453), int64(2), object(4)
memory usage: 46.7+ MB


In [19]:
# re merge the aggregated team stats to the games dataset
super_detailed_games_df = pd.merge(
    left=all_detailed_games_df[all_detailed_games_df["Season"] >= 2003],
    right=team_agg_df2,
    on=["TeamID", "Season", "League"],
    how="left",
    validate="m:1",
)

super_detailed_games_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 377608 entries, 0 to 377607
Columns: 508 entries, Season to ChalkSeed
dtypes: float64(453), int64(48), object(7)
memory usage: 1.4+ GB


In [20]:
super_detailed_games_df["OppTeamID"]

0         1328
1         1393
2         1437
3         1457
4         1208
          ... 
377603    3376
377604    3439
377605    3234
377606    3261
377607    3261
Name: OppTeamID, Length: 377608, dtype: int64

In [21]:
opp_chalk_seed_map = team_conf_seeds_df.groupby("TeamID")["ChalkSeed"].last()

super_detailed_games_df["OppChalkSeed"] = super_detailed_games_df["OppTeamID"].map(
    opp_chalk_seed_map
)

super_detailed_games_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 377608 entries, 0 to 377607
Columns: 509 entries, Season to OppChalkSeed
dtypes: float64(454), int64(48), object(7)
memory usage: 1.4+ GB


In [22]:
super_detailed_games_df["ChalkSeedDiff"] = (
    super_detailed_games_df["OppChalkSeed"] - super_detailed_games_df["ChalkSeed"]
)

0         2.0
1        -4.0
2         1.0
3         NaN
4        -9.0
         ... 
377603    1.0
377604    2.0
377605   -1.0
377606   -2.0
377607   -1.0
Name: ChalkSeedDiff, Length: 377608, dtype: float64

## Save New Data

In [23]:
# save all aggregated teams dataframe as well as the super deatiled games dataframe
team_agg_df.to_csv(os.path.join(DATA_DIR, "AllTeamsAgg.csv"))

In [24]:
super_detailed_games_df.to_csv(os.path.join(DATA_DIR, "AllSuperDetailedGames.csv"))